# Signal Processing (ECE-Y253)

## Electrical and Computer Engineering Department  
### University of Patras, Greece  

**Instructor:** Konstantinos Chatzilygeroudis  
**Email:** [costashatz@upatras.gr](mailto:costashatz@upatras.gr)

### Hands‑on Spectral Analysis & Filtering Lab
**Story:** *We observe a sampled signal that contains a few hidden sinusoidal tones, but it is corrupted by **colored (AR) noise**. Our job is to reveal the tones.*

This single notebook ties together Lectures **6–10**:

- **Lec 6:** Sampling & aliasing, DFT/FFT, spectral interpretation  
- **Lec 7:** Windowing, leakage, WSS processes, PSD, correlations, LTI view  
- **Lec 8:** Periodogram / Welch PSD, bias–variance tradeoff, AR models & Yule–Walker  
- **Lec 9–10:** White vs colored noise, FIR/IIR filtering, notch/band‑pass, stability, examples  

> The notebook is self‑contained: all signals are generated synthetically so that you can reproduce everything.


## 0. Imports & helper functions
We will use only NumPy, SciPy, and Matplotlib.


In [ ]:
import numpy as np
import scipy.signal as sp
import scipy
import matplotlib.pyplot as plt

# np.random.seed(7) # uncomment for reproducibility

def db(x, eps=1e-12):
    return 20*np.log10(np.maximum(np.abs(x), eps))

def plot_fft(x, fs, title="", ax=None):
    N = len(x)
    X = np.fft.rfft(x)
    f = np.fft.rfftfreq(N, d=1/fs)
    if ax is None:
        fig, ax = plt.subplots()
    ax.plot(f, db(X))
    ax.set_xlabel("Frequency (Hz)")
    ax.set_ylabel(r"$|X(f)|$ [dB]")
    ax.set_title(title)
    ax.grid(True)
    return ax

def periodogram(x, fs, window="boxcar"):
    f, Pxx = sp.periodogram(x, fs=fs, window=window, scaling="density", detrend=False)
    return f, Pxx

def welch_psd(x, fs, nperseg=512, noverlap=256, window="hann"):
    f, Pxx = sp.welch(x, fs=fs, nperseg=nperseg, noverlap=noverlap,
                      window=window, detrend=False, scaling="density")
    return f, Pxx

def ar_yule_walker(x, p):
    # Estimate AR(p) using biased autocorrelation + Yule–Walker
    r = sp.correlate(x, x, mode="full", method="auto")
    mid = len(r)//2
    r = r[mid:mid+p+1] / len(x)  # biased estimate r[0..p]
    R = scipy.linalg.toeplitz(r[:-1])
    a = np.linalg.solve(R, -r[1:])  # AR coeffs (without leading 1)
    sigma2 = r[0] + np.dot(a, r[1:])
    return a, sigma2

def ar_psd(a, sigma2, fs, nfft=2048):
    # PSD of AR model: sigma2 / |1 + sum a_k e^{-jwk}|^2
    w = np.linspace(0, np.pi, nfft)
    A = 1 + np.sum([a[k]*np.exp(-1j*w*(k+1)) for k in range(len(a))], axis=0)
    S = sigma2 / (np.abs(A)**2)
    f = w/(2*np.pi)*fs
    return f, S


## 1. Generate the *analog* signal and sample it

### 1.1 Continuous‑time model
We imagine an analog signal made of $K$ tones:
$$
x_c(t) = \sum_{k=1}^K A_k\cos(2\pi f_k t + \phi_k).
$$

Sampling with period $T_s$ (rate $f_s=1/T_s$) gives the discrete‑time signal
$$
x[n] = x_c(nT_s).
$$

### 1.2 Where aliasing comes from (quick derivation)
A single tone $x_c(t)=\cos(2\pi f_0 t)$ becomes
$$
x[n]=\cos\!\left(2\pi f_0 nT_s\right)=\cos\!\left(2\pi \frac{f_0}{f_s} n\right).
$$
Because discrete‑time frequency is periodic with period $1$ in $f_0/f_s$,
$$
\cos\!\left(2\pi\left(\frac{f_0}{f_s}+m\right)n\right)=\cos\!\left(2\pi \frac{f_0}{f_s}n\right),\quad m\in\mathbb{Z}.
$$
So any $f_0$ and $f_0+m f_s$ produce identical samples. The observed **alias** within $[0,f_s/2]$ is
$$
f_{\text{alias}}=\left|f_0-mf_s\right|.
$$


In [ ]:
# True analog tones (Hz)
tones_hz = [55, 140, 310]   # 310 Hz will alias for low fs
amps = [1.0, 0.8, 0.5]
phases = [0.1, 1.1, -0.7]

def sample_tones(fs, T=3.04):
    t = np.arange(0, T, 1/fs)
    x = np.zeros_like(t)
    for A, f, ph in zip(amps, tones_hz, phases):
        x += A*np.cos(2*np.pi*f*t + ph)
    return t, x

fs_low  = 400   # Nyquist = 200 Hz -> 310 Hz aliases
fs_high = 2000  # Nyquist = 1000 Hz -> no aliasing

tL, xL = sample_tones(fs_low)
tH, xH = sample_tones(fs_high)

fig, axs = plt.subplots(2,1, figsize=(8,5), sharex=False)
plot_fft(xL, fs_low,  "FFT magnitude, $f_s=400$ Hz (aliasing expected)", ax=axs[0])
plot_fft(xH, fs_high, "FFT magnitude, $f_s=2000$ Hz (no aliasing)", ax=axs[1])
plt.tight_layout()
plt.show()


**Discussion**
- At $f_s=400$ Hz, the 310 Hz tone aliases to $|310-400|=90$ Hz.  
- At $f_s=2000$ Hz, all tones sit at their true frequencies.

From here on we use $f_s=2000$ Hz.


## 2. Add **colored noise** (AR process)

### 2.1 White vs colored
- **White noise:** flat PSD, $S_{ww}(f)=\sigma^2$.  
- **Colored noise:** PSD shaped by dynamics (more energy in some bands).

### 2.2 AR(2) noise model
We generate colored noise using an AR(2) process:
$$
v[n] + a_1 v[n-1] + a_2 v[n-2] = e[n],\quad e[n]\sim\mathcal{N}(0,\sigma_e^2).
$$

Taking the DTFT of both sides:
$$
V(e^{j\omega})\Bigl(1+a_1 e^{-j\omega}+a_2 e^{-j2\omega}\Bigr)=E(e^{j\omega}).
$$
Thus the **noise shaping** transfer function is
$$
H_v(e^{j\omega})=\frac{V}{E}=\frac{1}{1+a_1 e^{-j\omega}+a_2 e^{-j2\omega}},
$$
and because $e[n]$ is white with PSD $\sigma_e^2$,
$$
S_{vv}(e^{j\omega}) = |H_v(e^{j\omega})|^2 \sigma_e^2
= \frac{\sigma_e^2}{\left|1+a_1 e^{-j\omega}+a_2 e^{-j2\omega}\right|^2}.
$$


In [ ]:
fs = fs_high
t, x_clean = tH, xH

# Stable AR(2) colored noise coefficients
r = 0.9
theta = 0.4*np.pi
a_true = np.array([-2*r*np.cos(theta), r**2])  # stable
sigma_e2_true = 0.2

# Generate AR noise: v + a1 v[n-1] + a2 v[n-2] = e
e = np.sqrt(sigma_e2_true) * np.random.randn(len(t))
v = sp.lfilter([1.0], np.r_[1.0, a_true], e)  # denominator = [1, a1, a2]

snr_db = -5.  # pretty noisy
Px = np.mean(x_clean**2)
Pv = np.mean(v**2)
v = v * np.sqrt(Px/(Pv*10**(snr_db/10)))

x_obs = x_clean + v

fig, axs = plt.subplots(2,1, figsize=(9,5), sharex=True)
axs[0].plot(t, x_clean, lw=1)
axs[0].set_title("Clean signal (time domain)")
axs[0].set_xlim(0, 0.2)
axs[0].grid(True)

axs[1].plot(t, x_obs, lw=1)
axs[1].set_title("Observed signal = tones + colored noise")
axs[1].grid(True)
axs[1].set_xlabel("Time (s)")
plt.tight_layout()
plt.show()


## 3. DFT/FFT view + windowing & leakage

### 3.1 DFT definition and frequency bins
For $N$ samples, the DFT is
$$
X[k] = \sum_{n=0}^{N-1} x[n] e^{-j 2\pi kn/N},\quad k=0,\dots,N-1.
$$
Each bin corresponds to frequency
$$
f_k = k\frac{f_s}{N}.
$$

### 3.2 Windowing and leakage intuition
Multiplying by $w[n]$ in time corresponds to convolution in frequency:
$$
X_w(e^{j\omega}) = \frac{1}{2\pi}\,X(e^{j\omega}) * W(e^{j\omega}).
$$
So the window’s spectrum $W$ "smears" peaks → **leakage**.  
Lower side‑lobes in $W$ reduce leakage, but wider main‑lobes reduce resolution.

We'll compare:
- Rectangular (boxcar)  
- Hann


In [ ]:
N = len(x_obs)

fig, axs = plt.subplots(2,1, figsize=(9,5), sharex=True)
ax0 = plot_fft(x_obs, fs, "FFT with rectangular window (implicit)", ax=axs[0])

x_hann = x_obs * sp.windows.hann(N, sym=False)
ax1 = plot_fft(x_hann, fs, "FFT with Hann window", ax=axs[1])

plt.tight_layout()
plt.show()


**What to notice**
- The Hann window reduces leakage (lower side‑lobes).
- Peaks are a bit wider (main‑lobe widening).

This motivates PSD estimation methods.


## 4. PSD estimation: Periodogram vs Welch

### 4.1 Periodogram
Using a window $w[n]$, the (one‑sided) periodogram is
$$
\hat S_{xx}^{\text{per}}(f_k)=\frac{1}{N f_s U}\,|X_w[k]|^2,
$$
where $X_w$ is the DFT of $x[n]w[n]$ and
$$
U=\frac{1}{N}\sum_{n=0}^{N-1}w^2[n]
$$
normalizes the window power.

**Properties:** high resolution, high variance (does **not** decrease with $N$).

### 4.2 Welch’s method
Split the data into $M$ overlapping segments of length $L$,
compute a windowed periodogram per segment, then average:
$$
\hat S_{xx}^{\text{Welch}}(f) = \frac{1}{M}\sum_{m=1}^M \hat S_{xx,m}^{\text{per}}(f).
$$
Averaging reduces variance roughly by $\sim 1/M$, but resolution is controlled by $L$.


In [ ]:
f_per, P_per = periodogram(x_obs, fs, window="hann")
f_w1, P_w1  = welch_psd(x_obs, fs, nperseg=2048, noverlap=1024)
f_w2, P_w2  = welch_psd(x_obs, fs, nperseg=512,  noverlap=256)

plt.figure(figsize=(9,4))
plt.semilogy(f_per, P_per, label="Periodogram (Hann)")
plt.semilogy(f_w1,  P_w1,  label="Welch, long segments (better res)")
plt.semilogy(f_w2,  P_w2,  label="Welch, short segments (lower var)")
plt.xlim(0, 500)
plt.xlabel("Frequency (Hz)")
plt.ylabel("PSD")
plt.title("PSD estimates: bias–variance tradeoff")
plt.grid(True)
plt.legend()
plt.tight_layout()
plt.show()


**Discussion**
- The periodogram is jagged (high variance).  
- Welch smooths by averaging; shorter segments smooth more but blur close peaks.

Next, we model the **noise floor** with AR estimation.


## 5. AR modeling of the colored noise (Yule–Walker)

### 5.1 AR($p$) definition
$$
x[n] + \sum_{k=1}^{p} a_k x[n-k] = e[n],\quad e[n]\sim\text{WN}(0,\sigma_e^2).
$$

### 5.2 Autocorrelation structure
For a WSS process, define
$$
r_x[\ell]=\mathbb{E}\{x[n]x[n-\ell]\}.
$$
Multiply the AR equation by $x[n-\ell]$ and take expectations:
$$
r_x[\ell] + \sum_{k=1}^p a_k\, r_x[\ell-k] = 0,\quad \ell=1,\dots,p.
$$
This yields **Yule–Walker** in matrix form:
$$
\begin{bmatrix}
r_x[0] & r_x[1] & \dots & r_x[p-1]\\
r_x[1] & r_x[0] & \dots & r_x[p-2]\\
\vdots & \vdots & \ddots & \vdots\\
r_x[p-1]& r_x[p-2]&\dots& r_x[0]
\end{bmatrix}
\begin{bmatrix}
a_1\\ \vdots\\ a_p
\end{bmatrix}
= -
\begin{bmatrix}
r_x[1]\\ \vdots\\ r_x[p]
\end{bmatrix}.
$$
We estimate $r_x[\ell]$ from data, solve for $a_k$, then estimate $\sigma_e^2$ from
$$
\sigma_e^2 = r_x[0]+\sum_{k=1}^p a_k r_x[k].
$$

### 5.3 AR PSD
The AR transfer function is
$$
H(e^{j\omega})=\frac{1}{1+\sum_{k=1}^p a_k e^{-j\omega k}},
$$
so
$$
\hat S_{xx}^{\text{AR}}(\omega) = \frac{\hat\sigma_e^2}{\left|1+\sum_{k=1}^p \hat a_k e^{-j\omega k}\right|^2}.
$$


In [ ]:
# Estimate AR(p) on *noise only* (for teaching clarity)
p = 2
a_hat, sigma_hat = ar_yule_walker(v, p)

print("True AR coeffs:", a_true)
print("Estimated AR coeffs:", a_hat)
print("True sigma_e^2:", sigma_e2_true, "Estimated:", sigma_hat)

f_ar, S_ar = ar_psd(a_hat, sigma_hat, fs)
S_ar = S_ar / fs   # convert to power/Hz to match Welch

# Compare AR PSD to Welch PSD of v
f_v_w, P_v_w = welch_psd(v, fs, nperseg=2048, noverlap=1024)

plt.figure(figsize=(9,4))
plt.semilogy(f_v_w, P_v_w, label="Welch PSD of noise")
plt.semilogy(f_ar,  S_ar,  label=f"AR({p}) PSD (Yule–Walker)")
plt.xlim(0, 500)
plt.xlabel("Frequency (Hz)")
plt.ylabel("PSD")
plt.title("AR model matches the colored noise spectrum")
plt.grid(True)
plt.legend()
plt.tight_layout()
plt.show()


**Takeaway:** An AR model provides a compact parametric PSD with low variance.

But in practice we *do not* have access to the noise alone.  
The next section shows how to estimate an AR model directly from $x_{\text{obs}}$.


## 6. AR estimation **from the observed signal** (realistic case)

We now estimate AR($p$) from **$x_{\text{obs}}$**, which contains tones + noise.

### 6.1 Why this is harder
The AR model tries to explain *all* structure in $x_{\text{obs}}$ as an AR process.  
Strong tones can bias the autocorrelation, so the AR fit may partially "absorb" the tones into the noise model. This can reduce whitening quality.

A common practical trick is:
1. estimate AR on $x_{\text{obs}}$ anyway,  
2. whiten,  
3. optionally re‑estimate after removing detected tones (iterative refinement).

We'll do step (1–2) to compare with the ideal noise‑only case.


In [ ]:
p_obs = 6  # slightly higher order helps capture colored background
a_hat_obs, sigma_hat_obs = ar_yule_walker(x_obs, p_obs)

print("AR coeffs estimated on x_obs:", np.round(a_hat_obs, 4))

f_ar_obs, S_ar_obs = ar_psd(a_hat_obs, sigma_hat_obs, fs)
S_ar_obs = S_ar_obs / fs   # convert to power/Hz to match Welch
f_x_w, P_x_w = welch_psd(x_obs, fs, nperseg=1024, noverlap=512)

plt.figure(figsize=(9,4))
plt.semilogy(f_x_w, P_x_w, label="Welch PSD of x_obs")
plt.semilogy(f_ar_obs, S_ar_obs, label=f"AR({p_obs}) PSD fit on x_obs")
plt.xlim(0, 500)
plt.xlabel("Frequency (Hz)")
plt.ylabel("PSD")
plt.title("AR PSD estimated from observed signal")
plt.grid(True)
plt.legend()
plt.tight_layout()
plt.show()


### 6.2 Whitening using AR($p$) from $x_{\text{obs}}$
The whitening filter is
$$
H_w(z)=1+\sum_{k=1}^{p} \hat a_k z^{-k}.
$$
We compare whitening outcomes:
- **Ideal:** AR estimated from noise only (previous section).  
- **Realistic:** AR estimated from $x_{\text{obs}}$.


In [ ]:
# Whitening filter from AR estimated on x_obs
Hw_b_obs = np.r_[1.0, a_hat_obs]
x_white_obs = sp.lfilter(Hw_b_obs, [1.0], x_obs)

fig, axs = plt.subplots(3,1, figsize=(9,7), sharex=True)
plot_fft(x_obs, fs, "Observed spectrum (before whitening)", ax=axs[0])
plot_fft(sp.lfilter(np.r_[1.0, a_hat], [1.0], x_obs), fs,
         "Whitening using AR from noise‑only (ideal)", ax=axs[1])
plot_fft(x_white_obs, fs,
         "Whitening using AR from x_obs (realistic)", ax=axs[2])
for ax in axs:
    ax.set_xlim(0, 500)
plt.tight_layout()
plt.show()


**Observation:** Whitening from $x_{\text{obs}}$ still helps, but may leave residual coloration or slightly suppress tones.

We will proceed with the *realistic* whitened signal for peak picking, since that's the case students face in real data.


## 7. Peak picking after realistic whitening


In [ ]:
Nw = len(x_white_obs)
Xw = np.fft.rfft(x_white_obs * sp.windows.hann(Nw, sym=False))
f = np.fft.rfftfreq(Nw, d=1/fs)
mag = np.abs(Xw)

peaks, props = sp.find_peaks(mag, height=np.max(mag)*0.3, distance=50)
est_freqs = f[peaks]
print(est_freqs)

plt.figure(figsize=(9,3))
plt.plot(f, db(mag))
plt.plot(est_freqs, db(mag[peaks]), "x", ms=8)
plt.xlim(0, 500)
plt.xlabel("Frequency (Hz)")
plt.ylabel("Magnitude [dB]")
plt.title("Peak picking after realistic whitening")
plt.grid(True)
plt.tight_layout()
plt.show()

print("Estimated tone frequencies (Hz):", np.round(est_freqs, 2))


## 8. Design a band‑pass FIR to isolate the tones

We build a **multi‑band FIR** that keeps energy around the detected peaks.

### 8.1 FIR via windowed‑sinc
An ideal low‑pass at cutoff $f_c$ has impulse response
$$
h_{\text{lp}}[n]=2\frac{f_c}{f_s}\,\mathrm{sinc}\!\left(2\frac{f_c}{f_s}(n-n_0)\right).
$$
A band‑pass between $f_1$ and $f_2$ is the difference of two low‑passes:
$$
h_{\text{bp}}[n]=h_{\text{lp},f_2}[n]-h_{\text{lp},f_1}[n],
$$
then we window it to control ripples and sidelobes.

We'll use `firwin2` to implement this shape directly.


In [ ]:
bands = [(f-10, f+10) for f in est_freqs]

freqs = [0]
gains = [0]
for (f1, f2) in bands:
    freqs += [f1-5, f1, f2, f2+5]
    gains += [0, 1, 1, 0]
freqs += [fs/2]
gains += [0]

freqs = np.clip(freqs, 0, fs/2)
freqs_norm = np.array(freqs) / (fs/2)

numtaps = 801
h_fir = sp.firwin2(numtaps, freqs_norm, gains, window="hann")

# x_rec = sp.lfilter(h_fir, [1.0], x_obs)
x_rec = sp.filtfilt(h_fir, [1.0], x_obs)

w, H = sp.freqz(h_fir, worN=4096)
fH = w/(2*np.pi)*fs

plt.figure(figsize=(9,3))
plt.plot(fH, db(H))
plt.xlim(0, 500)
plt.ylim(-80, 5)
plt.xlabel("Frequency (Hz)")
plt.ylabel(r"$|H(f)|$ [dB]")
plt.title("Designed multi‑band FIR response")
plt.grid(True)
plt.tight_layout()
plt.show()

fig, axs = plt.subplots(2,1, figsize=(9,5), sharex=True)
plot_fft(x_obs, fs, "Spectrum before FIR recovery", ax=axs[0])
plot_fft(x_rec, fs, "Spectrum after FIR recovery", ax=axs[1])
axs[0].set_xlim(0, 500); axs[1].set_xlim(0, 500)
plt.tight_layout()
plt.show()


## 9. Time‑domain comparison


In [ ]:
plt.figure(figsize=(9,4))
plt.plot(t, x_clean, label="Clean (ground truth)", lw=2, alpha=0.8)
plt.plot(t, x_obs,   label="Observed", lw=1, alpha=0.6)
plt.plot(t, x_rec,   label="Recovered (FIR)", lw=1.5)
# plt.xlim(0, 0.25)
plt.xlim(2., 2.25)
plt.xlabel("Time (s)")
plt.ylabel("Amplitude")
plt.title("Recovery in time domain (zoomed)")
plt.grid(True)
plt.legend()
plt.tight_layout()
plt.show()


## 10. Summary
This lab showcased the full spectral toolchain: sampling can create aliasing if Nyquist is violated; the DFT reveals tones but is sensitive to leakage, which windows mitigate. PSD estimation via Welch trades resolution for variance reduction. Parametric AR modeling compactly captures the colored‑noise PSD with low variance. Even when AR parameters are estimated from the observed data (realistic case), whitening flattens the noise floor enough for reliable peak detection. Finally, a designed multi‑band FIR recovers the hidden tones in both frequency and time domains.
